In [31]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import json
from collections import defaultdict

from IPython.display import HTML
from IPython.display import display_html

%load_ext autoreload
%autoreload 2

import sys
sys.path.append("..")
from utils.utils import *
import os


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [32]:
#FN = "../raw_views_filters_2021-12-15.ss.csv"
INP_FIELD = "NormInputHashCode"
FILTER_FIELD = "FilterExpr"
DEDUP_FIELDS = [INP_FIELD, FILTER_FIELD]

FN = "../data/cosmos14/raw_views_filters_2021-12-15.ss.csv"
DEDUPFN = FN.replace(".ss.csv", "-dedup.ss.csv")
#INP_FIELD = "HashTagInput"

In [33]:
#df = pd.read_csv(FN, sep="|")
#df = pd.read_csv(FN, sep="\t")
import time
start = time.time()
if os.path.exists(DEDUPFN):
    df = pd.read_csv(DEDUPFN, sep="\t")
else:
    df = pd.read_csv(FN, sep="\t")
    
print("took: ", time.time()-start)

took:  38.878005504608154


In [34]:
print(len(df))

3142169


In [35]:
#df = df.rename(columns={"#Field:JobGUID":"jobid"})
df = df.rename(columns={"JobGUID":"jobid"})

In [36]:
print(df.keys())

Index(['jobid', 'HashTagInput', 'OperatorName', 'EstCardinality',
       'InputCardinality', 'NormInputHashCode', 'RowCount', 'Selectivity',
       'ExclusiveTime', 'StageName', 'VertexCount', 'FilterExpr'],
      dtype='object')


In [37]:
# For some analysis, we may not want to drop duplicates here.

## not sure why this drops so many too; same job, multiple filters on same table is possible, but why is it so common?
#df = df.drop_duplicates(["jobid", INP_FIELD])

df = df.drop_duplicates(DEDUP_FIELDS)

In [38]:
print(len(df))

3142169


In [40]:
df["FilterExpr"].values[10]

'{"isComparison":false,"expOperator":"And","attribute":{"name":"","dataType":""},"values":[],"children":[{"isComparison":true,"expOperator":"=","attribute":{"name":"TenantId:80","dataType":"String"},"values":["\\"a5f09c7a-de93-499f-b1b3-28982871fa33\\""],"children":[],"isSorted":false},{"isComparison":true,"expOperator":"=","attribute":{"name":"FinalFilterVerdict:94","dataType":"String"},"values":["\\"Malware\\""],"children":[],"isSorted":false},{"isComparison":false,"expOperator":null,"attribute":{"name":"","dataType":""},"values":[],"children":[{"isComparison":true,"expOperator":"string.IsNullOrEmpty(FinalVerdict)","attribute":{"name":"","dataType":""},"values":[],"children":[],"isSorted":false}],"isSorted":false},{"isComparison":false,"expOperator":null,"attribute":{"name":"","dataType":""},"values":[],"children":[{"isComparison":true,"expOperator":"string.IsNullOrEmpty(FinalFilterVerdict)","attribute":{"name":"","dataType":""},"values":[],"children":[],"isSorted":false}],"isSorted"

# Duplicate and then execute ---> we could group these together, but probably won't make a big difference in the stats we collect

In [41]:
df["InputCardinality"] = df.apply(lambda x: max(1, x["InputCardinality"]), axis=1)

In [42]:
df["Selectivity"] = df.apply(lambda x: min(x["RowCount"] / x["InputCardinality"], 1.0) ,axis=1)

In [51]:
start = time.time()
parse_filter_exprs(df, INP_FIELD, FILTER_FIELD)
print("took: ", time.time()-start)

final num decode errors:  868
took:  755.384179353714


# Select example data to recreate rows

# Plotting discrete constants per table

In [52]:
inpdiscdata = defaultdict(list)
COLS_TO_COPY = ["Selectivity", "ExclusiveTime"]

for idx, row in df.iterrows():
    if row["discrete_ops"] == 0:
        continue 
    if row["cont_ops"] != 0:
        continue    
    if row["like_ops"] != 0:
        continue  
    if row["in_ops"] != 0:
        continue     
    if row["complex_ops"] != 0:
        continue
    if row["null_checks"] != 0:
        continue
        
    types_all = row["types_all"]
    if types_all.count(",") > 1:
        continue
    
    if row["discrete_type"] == "null":
        continue
    
    expr = row[FILTER_FIELD]
    d = json.loads(expr)
    filter_values = extract_values(d, "values")
    #print(filter_values)
#    if len(filter_values) > 1:
#         print(row["types_all"])
#         print(d)
#         print(filter_values)
    #print(filter_values)
    col_names = extract_values(d, "name")
    
    for fi, fvs in enumerate(filter_values):
        if len(fvs) == 0:
            continue
        #assert len(fvs) == 1
#         if len(fvs) != 1:
#             print(fvs)
        assert fvs[0] != "null"
        
        disctype = get_discrete_type(fvs)
        
        inpdiscdata["input"].append(row[INP_FIELD])
        inpdiscdata["col"].append(col_names[fi])
        inpdiscdata["const"].append(fvs[0])
        inpdiscdata["disctype"].append(disctype)
        
        for ck in COLS_TO_COPY:
            inpdiscdata[ck].append(row[ck])
            
        #inpdiscdata["Selectivity"].append(row["Selectivity"])
        

In [53]:
print(len(inpdiscdata["input"]))
discdf = pd.DataFrame(inpdiscdata)
print(discdf["input"].describe())
print(discdf["const"].describe())

58601
count    5.860100e+04
mean    -1.115727e+08
std      1.348025e+09
min     -2.146069e+09
25%     -1.585603e+09
50%     -1.230045e+08
75%      1.224087e+09
max      2.145888e+09
Name: input, dtype: float64
count     58601
unique     3449
top       false
freq       4621
Name: const, dtype: object


In [54]:
print(discdf["Selectivity"].describe())

count    5.860100e+04
mean     9.511534e-02
std      2.320440e-01
min      0.000000e+00
25%      3.191254e-08
50%      3.807082e-04
75%      5.232076e-02
max      1.000000e+00
Name: Selectivity, dtype: float64


In [55]:
discinps = discdf.groupby(["input","col"])["const"].count().reset_index().sort_values(by="const", 
                                                                    ascending=False)
discinps = discinps[discinps["const"] >= 2]
discinps = discinps.drop_duplicates("input")
inpnames = discinps["input"].values
print(len(inpnames))

323


In [56]:
# df2 = discdf[discdf.input.isin(inpnames)]
# df2["const"].values

In [72]:
import random

def plot_col_vals(inps, df, pkind, fn):
    fig, axs = plt.subplots(nrows=3,ncols=5,figsize=(30,12))
    assert len(inps) <= 15
    for i, (inp, column) in enumerate(inps):
        tmpdf1 = discdf[discdf.input == inp]
        tmpdf1 = tmpdf1[tmpdf1.col == column]
        row = i // 5
        figcol = i % 5
        ax = axs[row][figcol]
        vals = {}

## shortening each string so its visible + adding random number to 
        consts = set(tmpdf1["const"])
        for const in consts:
            vals[const] = str(random.randint(0,10)) + "-" + const[0:6]           
        tmpdf1["const"] = tmpdf1.apply(lambda x: vals[x["const"]], axis=1)
        
        if pkind == "Count":
            sns.countplot(data=tmpdf1, x="const", 
                          hue="const", 
                          ax=ax, dodge=False)
        elif pkind == "Selectivity":
            sns.barplot(data=tmpdf1, x="const", 
              hue="const", y = "Selectivity",
              ax=ax, dodge=False)
        
        ax.set_xlabel("Constant", fontsize=14)
        ax.set_ylabel(pkind, fontsize=14)
        ax.legend().remove()
    #plt.show()
    plt.savefig(fn, bbox_inches="tight")
    plt.close()
    
def plot_all_inputs(inpnames, discdf, prefix):
    inps = []
    resets = 1
    for i, inp in enumerate(inpnames):
        print(i)
        tmpdf1 = discdf[discdf.input == inp]
        cols = set(tmpdf1["col"].values)
        for col in cols:
            tmpdf2 = tmpdf1[tmpdf1.col == col]
            numc = len(set(tmpdf2["const"].values))
            if numc < 2:
                #print("continue")
                continue
            if numc > 30:
                continue
                
            inps.append((inp, col))

            if len(inps) == 15:
                fn = prefix + "-Selectivities-" + str(resets) + ".png"
                fn2 = prefix + "-Counts-" + str(resets) + ".png"
                plot_col_vals(inps, discdf, "Selectivity", fn)
                #plot_col_vals(inps, discdf, "Count", fn2)
                resets += 1
                inps = []

In [73]:
plot_all_inputs(inpnames, discdf, "Discrete1")

0
1
2
3
4
5
6
7
8
9
10
11
12
Discrete1-Counts-1.png
13
14
15
16
17
18
19
20
21
22
23
24
Discrete1-Counts-2.png
25
26
Discrete1-Counts-3.png
Discrete1-Counts-4.png
27
28
29
30
31
32
33
34
35
Discrete1-Counts-5.png
Discrete1-Counts-6.png
Discrete1-Counts-7.png
Discrete1-Counts-8.png
36
37
38
39
40
41
Discrete1-Counts-9.png
42
Discrete1-Counts-10.png
Discrete1-Counts-11.png
Discrete1-Counts-12.png
Discrete1-Counts-13.png
Discrete1-Counts-14.png
Discrete1-Counts-15.png
Discrete1-Counts-16.png
43
44
45
46
47
48
49
50
Discrete1-Counts-17.png
51
52
Discrete1-Counts-18.png
Discrete1-Counts-19.png
Discrete1-Counts-20.png
53
Discrete1-Counts-21.png
Discrete1-Counts-22.png
54
Discrete1-Counts-23.png
Discrete1-Counts-24.png
Discrete1-Counts-25.png
Discrete1-Counts-26.png
Discrete1-Counts-27.png
55
56
Discrete1-Counts-28.png
Discrete1-Counts-29.png
Discrete1-Counts-30.png
Discrete1-Counts-31.png
57
58
59
Discrete1-Counts-32.png
Discrete1-Counts-33.png
60
61
62
63
64
Discrete1-Counts-34.png
65
66
67

# Cont + discrete

In [73]:
inpdiscdata2 = defaultdict(list)
COLS_TO_COPY = ["Selectivity", "ExclusiveTime", "RowCount"]

for idx, row in df.iterrows():
    if row["discrete_ops"] == 0:
        continue 
    if row["cont_ops"] == 0:
        continue    

    if row["like_ops"] != 0:
        continue  
    if row["in_ops"] != 0:
        continue     
    if row["complex_ops"] != 0:
        continue
    if row["null_checks"] != 0:
        continue
        
    types_all = row["types_all"]

#     if types_all.count(",") > 1:
#         continue
    
    if row["discrete_type"] == "null":
        continue

    expr = row[FILTER_FIELD]
    d = json.loads(expr)
    filter_values = extract_values(d, "values")

    col_names = extract_values(d, "name")
    ops = extract_values(d, "expOperator")
    
    for fi, fvs in enumerate(filter_values):
        if len(fvs) == 0:
            continue
        assert len(fvs) == 1
        
        if "<" in ops[fi] or ">" in ops[fi]:
            continue
        if col_names[fi] == "":
            continue
            
        if "System" in fvs[0]:
            continue
        
        disctype = get_discrete_type(fvs)
        inpdiscdata2["input"].append(row[INP_FIELD])
        inpdiscdata2["col"].append(col_names[fi])
        inpdiscdata2["const"].append(fvs[0])
        inpdiscdata2["disctype"].append(disctype)
        
        for ck in COLS_TO_COPY:
            inpdiscdata2[ck].append(row[ck])
        

In [74]:
print(len(inpdiscdata2["input"]))
discdf = pd.DataFrame(inpdiscdata2)
print(discdf["input"].describe())
print(discdf["const"].describe())
print(discdf["disctype"].describe())

102768
count    1.027680e+05
mean    -2.347119e+08
std      1.281702e+09
min     -2.145225e+09
25%     -1.670314e+09
50%     -1.589033e+08
75%      8.755665e+08
max      2.140837e+09
Name: input, dtype: float64
count     102768
unique      1348
top         true
freq       19526
Name: const, dtype: object
count     102768
unique         4
top       string
freq       39608
Name: disctype, dtype: object


In [75]:
print(discdf["Selectivity"].describe())

count     102768
unique         2
top            0
freq      101660
Name: Selectivity, dtype: object


In [76]:
# tmp = discdf[discdf.disctype == "string"]
# print(tmp["const"].values)

In [77]:
discdf = discdf[discdf.disctype == "string"]
discinps = discdf.groupby(["input","col", "disctype"])["const"].nunique().reset_index().sort_values(by="const", 
                                                                    ascending=False)
discinps = discinps[discinps["const"] >= 1]
discinps = discinps.drop_duplicates("input")
inpnames = discinps["input"].values
print(len(inpnames))
HTML(discinps.head(20).to_html())

509


In [78]:
#print(inpnames)

In [79]:
df2 = discdf[discdf.input.isin(inpnames)]
# print(df2["const"].values)

In [80]:
# for inp in inpnames:
#     print(inp)
#     tmpdf = discdf[discdf.input == inp]
#     #print(tmpdf["disctype"].values)
#     fix, ax = plt.subplots(figsize=(10,10))
#     #sns.barplot(data=tmpdf, x="col", y = "Selectivity", hue="const", ax=ax, ci=None)
#     print(tmpdf["disctype"].values[0])
#     sns.barplot(data=tmpdf, x="col", y = "RowCount", hue="const", ax=ax, ci=None)
#     #plt.legend().remove()
#     plt.show()

# Allowing "In" predicates

In [82]:
inpdiscdata2 = defaultdict(list)
COLS_TO_COPY = ["Selectivity", "ExclusiveTime", "RowCount"]

for idx, row in df.iterrows():
    if row["discrete_ops"] == 0:
        continue 
        
    if row["cont_ops"] == 1:
        continue    

    if row["like_ops"] != 0:
        continue
        
#     if row["in_ops"] != 0:
#         continue     
    if row["complex_ops"] != 0:
        continue
    if row["null_checks"] != 0:
        continue
        
    types_all = row["types_all"]

    if row["discrete_type"] == "null":
        continue

    expr = row[FILTER_FIELD]
    d = json.loads(expr)
    filter_values = extract_values(d, "values")

    col_names = extract_values(d, "name")
    ops = extract_values(d, "expOperator")
    
#     if row["in_ops"] == 1:
#         print(col_names)
#         print(filter_values)
#         print("********")
        
    for fi, fvs in enumerate(filter_values):
        if len(fvs) == 0:
            continue
        #assert len(fvs) == 1
        
        if "<" in ops[fi] or ">" in ops[fi]:
            continue
        if col_names[fi] == "":
            continue
            
        if "System" in fvs[0]:
            continue
        
        disctype = get_discrete_type(fvs)
        inpdiscdata2["input"].append(row[INP_FIELD])
        inpdiscdata2["col"].append(col_names[fi])
        inpdiscdata2["const"].append(fvs[0])
        inpdiscdata2["disctype"].append(disctype)
        
        for ck in COLS_TO_COPY:
            inpdiscdata2[ck].append(row[ck])
        

In [83]:
print(len(inpdiscdata2["input"]))
discdf = pd.DataFrame(inpdiscdata2)
print(discdf["input"].describe())
print(discdf["const"].describe())
print(discdf["disctype"].describe())

1559063
count    1.559063e+06
mean     1.764672e+08
std      1.170868e+09
min     -2.146577e+09
25%     -8.879493e+08
50%      4.913155e+08
75%      1.097099e+09
max      2.147069e+09
Name: input, dtype: float64
count     1559063
unique      12647
top             1
freq        86360
Name: const, dtype: object
count     1559063
unique          4
top        string
freq      1153518
Name: disctype, dtype: object


In [84]:
discinps = discdf.groupby(["input","col"])["const"].count().reset_index().sort_values(by="const", 
                                                                    ascending=False)
discinps = discinps[discinps["const"] >= 2]
discinps = discinps.drop_duplicates("input")
inpnames = discinps["input"].values
print(len(inpnames))

5016


In [85]:
# for inp in inpnames:
#     tmpdf = discdf[discdf.input == inp]
#     fix, ax = plt.subplots(figsize=(10,10))
#     sns.barplot(data=tmpdf, x="col", y = "Selectivity", hue="const", ax=ax)
#     #plt.legend().remove()
#     plt.show()

In [86]:
# inps = []
# for inp in inpnames:
#     tmpdf1 = discdf[discdf.input == inp]
#     cols = set(tmpdf1["col"].values)
#     for col in cols:
#         tmpdf2 = tmpdf1[tmpdf1.col == col]
#         numc = len(set(tmpdf2["const"].values))
#         if numc < 2:
#             continue
#         inps.append((inp, col))
        
#         if len(inps) == 15:
#             plot_col_vals(inps, discdf, "sel")
#             plot_col_vals(inps, discdf, "count")
#             inps = []

In [ ]:
plot_all_inputs(inpnames, discdf, "In-")

In--Counts-1.png
In--Counts-2.png
In--Counts-3.png
In--Counts-4.png
In--Counts-5.png
In--Counts-6.png
In--Counts-7.png
In--Counts-8.png
In--Counts-9.png
In--Counts-10.png
In--Counts-11.png
In--Counts-12.png
In--Counts-13.png
In--Counts-14.png
In--Counts-15.png
In--Counts-16.png
In--Counts-17.png
In--Counts-18.png
In--Counts-19.png
In--Counts-20.png
In--Counts-21.png


/tmp/ipykernel_1999496/1953091886.py:5: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig, axs = plt.subplots(nrows=3,ncols=5,figsize=(30,12))


In--Counts-22.png
In--Counts-23.png
In--Counts-24.png
In--Counts-25.png
In--Counts-26.png
In--Counts-27.png
In--Counts-28.png
In--Counts-29.png
In--Counts-30.png
In--Counts-31.png
In--Counts-32.png
In--Counts-33.png
In--Counts-34.png
In--Counts-35.png
In--Counts-36.png
In--Counts-37.png
In--Counts-38.png
In--Counts-39.png
In--Counts-40.png
In--Counts-41.png
In--Counts-42.png
In--Counts-43.png
In--Counts-44.png
In--Counts-45.png
In--Counts-46.png
In--Counts-47.png
In--Counts-48.png
In--Counts-49.png
In--Counts-50.png
In--Counts-51.png
In--Counts-52.png
In--Counts-53.png
In--Counts-54.png
In--Counts-55.png
In--Counts-56.png
In--Counts-57.png
In--Counts-58.png
In--Counts-59.png
In--Counts-60.png
In--Counts-61.png
In--Counts-62.png
In--Counts-63.png
In--Counts-64.png
In--Counts-65.png
In--Counts-66.png
In--Counts-67.png
In--Counts-68.png
In--Counts-69.png
In--Counts-70.png
In--Counts-71.png
In--Counts-72.png
In--Counts-73.png
In--Counts-74.png
In--Counts-75.png
In--Counts-76.png
In--Counts

In [146]:
discdf.keys()

Index(['input', 'col', 'const', 'disctype', 'Selectivity', 'ExclusiveTime',
       'RowCount'],
      dtype='object')

# Number of constants used per table

In [156]:
def pretty_print(df):
    return display( HTML( df.to_html(index=False).replace("\\n","<br>") ) )

In [157]:
print(len(discdf))
discdf = discdf.drop_duplicates(["input", "col", "const"])
print(len(discdf))
discdf["dataset"] = "SCOPE"

pretty_print(discdf.groupby(["dataset","input", "col"])["const"].nunique().reset_index()[["dataset","const"]]\
    .groupby(["dataset"])[["const"]].describe(percentiles=[0.75,0.9,0.99]).reset_index()\
    .rename(columns={"count":"Total \\n Columns", "val":"Number of unique constants"})\
    .round(3))

#["const"].describe(percentiles=[0.75,0.9,0.99])

2911
2911


In [ ]:
STATCOLS = ["like_ops", "discrete_ops", "cont_ops"]
STATSTODROP = ["std", "min", "max", "25%", "50%","75%"]
curdrops = []

pretty_print(
    inpdata.groupby(["dataset", "col"]).nunique().reset_index()[["dataset","val"]]\
    .groupby(["dataset"])[["val"]].describe(percentiles=[0.75,0.9,0.99]).reset_index()\
    .rename(columns={"count":"Total \\n Columns", "val":"Number of unique constants"})\
    .round(3)
)

In [151]:
discdf.groupby(["input"])["const"].count().reset_index()["const"].describe(percentiles=[0.75,0.9,0.99])

count    714.000000
mean       4.077031
std        8.456535
min        1.000000
50%        2.000000
75%        4.000000
90%        8.000000
99%       30.740000
max      160.000000
Name: const, dtype: float64

# Continuous operators

In [143]:
contdata = defaultdict(list)
COLS_TO_COPY = ["Selectivity", "ExclusiveTime", "RowCount"]

for idx, row in df.iterrows():
    if row["discrete_ops"] != 0:
        continue 
        
    if row["cont_ops"] == 0:
        continue    

    if row["like_ops"] != 0:
        continue  
    if row["in_ops"] != 0:
        continue     
    if row["complex_ops"] != 0:
        continue
    if row["null_checks"] != 0:
        continue
        
    types_all = row["types_all"]

    if types_all.count(",") > 1:
        continue
    
    if row["discrete_type"] == "null":
        continue

    expr = row[FILTER_FIELD]
    d = json.loads(expr)
    filter_values = extract_values(d, "values")

    col_names = extract_values(d, "name")
    ops = extract_values(d, "expOperator")
    curdata = parse_cont_vals(ops, filter_values, col_names)
    print(curdata)
#     for fi, fvs in enumerate(filter_values):
#         if len(fvs) == 0:
#             continue
#         assert len(fvs) == 1
        
#         if "<" in ops[fi] or ">" in ops[fi]:
#             continue
#         if col_names[fi] == "":
#             continue
            
        
#         disctype = get_discrete_type(fvs)
#         inpdiscdata2["input"].append(row[INP_FIELD])
#         inpdiscdata2["col"].append(col_names[fi])
#         inpdiscdata2["const"].append(fvs[0])
#         inpdiscdata2["disctype"].append(disctype)
        
#         for ck in COLS_TO_COPY:
#             inpdiscdata2[ck].append(row[ck])
        

{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619305599.639801, 'comb_op': '', 

{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619480426.606468, 'comb_op': '', 

{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'': {'dtype': 'date', 'gt': 1619671855.806666, 'comb_op': '', 'cont_type': 'gt'}}
{'pa

{'EventReceivedDateTime:1': {'dtype': 'date', 'gt': 1572055200.0, 'comb_op': '', 'cont_type': 'gt'}}
{'EventReceivedDateTime:1': {'dtype': 'date', 'gt': 1572055200.0, 'comb_op': '', 'cont_type': 'gt'}}
{'time:3': {'dtype': 'date', 'lt': 1620440879.060319, 'comb_op': 'And', 'gt': 1617848879.060319, 'range': 2592000.0, 'cont_type': 'range'}}
{'partialRowNum0__:36': {'dtype': 'int', 'lt': 1, 'comb_op': '', 'cont_type': 'lt'}}
{'partialRowNum0__:42': {'dtype': 'int', 'lt': 1, 'comb_op': '', 'cont_type': 'lt'}}
{'A_ingest_time:28': {'dtype': 'date', 'gt': 1617839641.587829, 'comb_op': '', 'cont_type': 'gt'}}
{'partialRowNum0__:113': {'dtype': 'int', 'lt': 1, 'comb_op': '', 'cont_type': 'lt'}}
{'A_ingest_time:28': {'dtype': 'date', 'gt': 1616542303.241874, 'comb_op': '', 'cont_type': 'gt'}}
{'DeleteDateEvent:0': {'dtype': 'date', 'gt': 1608507226.079812, 'comb_op': '', 'cont_type': 'gt'}}
{'BaseDate:1': {'dtype': 'date', 'gt': 1615592225.500237, 'comb_op': '', 'cont_type': 'gt'}}
{'CreatedDa

{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620303290.347316, 'comb_op': '', 

...

{'A_ingest_time:28': {'dtype': 'date', 'gt': 1616972960.625581, 'comb_op': '', 'cont_type': 'gt'}}
{'EffectiveOnDate:167': {'dtype': 'date', 'lt': 1618743600.0, 'comb_op': 'And', 'gt': 1618704000.0, 'range': 39600.0, 'cont_type': 'range'}}
{'EffectiveOnDate:167': {'dtype': 'date', 'lt': 1618743600.0, 'comb_op': 'And', 'gt': 1618704000.0, 'range': 39600.0, 'cont_type': 'range'}}
{'IngestTime:8021': {'dtype': 'date', 'gt': 1616418000.0, 'comb_op': '', 'cont_type': 'gt'}}
{'partialRowNum0__:42': {'dtype': 'int', 'lt': 1, 'comb_op': '', 'cont_type': 'lt'}}
{'EndDate:5': {'dtype': 'date', 'gt': 1573516800.0, 'comb_op': '', 'cont_type': 'gt'}}
{'EndDate:5': {'dtype': 'date', 'gt': 1573516800.0, 'comb_op': '', 'cont_type': 'gt'}}
{'EffectiveOnDate:597': {'dtype': 'date', 'lt': 1618959600.0, 'comb_op': 'And', 'gt': 1618876800.0, 'range': 82800.0, 'cont_type': 'range'}}
{'ChatStartDateTime:12': {'dtype': 'date', 'gt': 1617321600.0, 'comb_op': '', 'cont_type': 'gt'}}
{'ChatStartDateTime:12': {'d

{'BaseDate:1': {'dtype': 'date', 'gt': 1614035351.808731, 'comb_op': '', 'cont_type': 'gt'}}
{'BaseDate:1': {'dtype': 'date', 'gt': 1613780204.373764, 'comb_op': '', 'cont_type': 'gt'}}
{'clientIngestTime:5': {'dtype': 'date', 'lt': 1619737200.0, 'comb_op': 'And', 'gt': 1619132400.0, 'range': 604800.0, 'cont_type': 'range'}}
{'IngestTime:8149': {'dtype': 'date', 'gt': 1617642000.0, 'comb_op': '', 'cont_type': 'gt'}}
{'DeleteDateEvent:0': {'dtype': 'date', 'gt': 1612566610.124962, 'comb_op': '', 'cont_type': 'gt'}}
{'partialRowNum0__:203': {'dtype': 'int', 'lt': 1, 'comb_op': '', 'cont_type': 'lt'}}
{'IngestTime:8277': {'dtype': 'date', 'gt': 1617915600.0, 'comb_op': '', 'cont_type': 'gt'}}
{'ChatStartDateTime:12': {'dtype': 'date', 'gt': 1616803200.0, 'comb_op': '', 'cont_type': 'gt'}}
{'ChatStartDateTime:12': {'dtype': 'date', 'gt': 1616803200.0, 'comb_op': '', 'cont_type': 'gt'}}
{'ChatStartDateTime:12': {'dtype': 'date', 'gt': 1616803200.0, 'comb_op': '', 'cont_type': 'gt'}}
{'ChatS

{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1618959958.036586, 'comb_op': '', 

{'CreatedDateTime:3': {'dtype': 'date', 'gt': 1616457600.0, 'comb_op': '', 'cont_type': 'gt'}}
{'CreatedDateTime:3': {'dtype': 'date', 'gt': 1616457600.0, 'comb_op': '', 'cont_type': 'gt'}}
{'CreatedDateTime:3': {'dtype': 'date', 'gt': 1616457600.0, 'comb_op': '', 'cont_type': 'gt'}}
{'CreatedDateTime:3': {'dtype': 'date', 'gt': 1616457600.0, 'comb_op': '', 'cont_type': 'gt'}}
{'CreatedDateTime:3': {'dtype': 'date', 'gt': 1616457600.0, 'comb_op': '', 'cont_type': 'gt'}}
{'CreatedDateTime:3': {'dtype': 'date', 'gt': 1616457600.0, 'comb_op': '', 'cont_type': 'gt'}}
{'Count:0': {'dtype': 'int', 'gt': 1, 'comb_op': '', 'cont_type': 'gt'}}
{'BuildNumber:2': {'dtype': 'int', 'lt': 25000, 'comb_op': 'And', 'gt': 21300, 'range': 3700, 'cont_type': 'range'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620515675.699973, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1620515675.699973, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'd

{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 'cont_type': 'lt'}}
{'MessageDateTime:498': {'dtype': 'date', 'lt': 1619651246.325873, 'comb_op': '', 